# 0184934-付子乾 —— 提取金融学院所有老师信息（正则版）

In [1]:
import re
import requests
from lxml import etree

global headers
headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:82.0) Gecko/20100101 Firefox/82.0'}
total_url = 'http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'      # 金融学院硕导首页界面
r_text = requests.get(total_url.format(1), headers=headers).text         # 首取第一页
html = etree.HTML(r_text)


### 提取页面的页码同样用的是之前的方法，这里不多介绍

In [2]:
# 提取硕导界面一共有多少页
num = html.xpath('//div[@class="bd_listabc"]//p/span[@class="num"]/text()')[0]
print(num)
page_num = int(re.findall(r".+/(\d)页", num, re.DOTALL)[0])
print(page_num)

共32条记录　1/3页
3


### 利用正则表达式匹配各个老师的信息

In [11]:
from IPython.display import display, HTML
import pandas as pd
List_info = []   # 用于存储每个老师的信息
for i in range(1, page_num+1):
    
    r_text = requests.get(total_url.format(i), headers=headers).text
    html = etree.HTML(r_text)
    urls = html.xpath('//div[@class="bd_listabc"]//li//div[@class="textlist"]/a/@href')

    for url in urls:
        resp = requests.get(url, headers=headers).text
        # 一般情形的处理，利用sub将所有的html标签转化为空格
        repl_resp = re.sub('<.+?>', ' ', resp).replace('\u3000','').replace('\u200b','').replace('\xa0','').replace('&nbsp;','')
        
        symbol = '：'
        Basic_info = {'姓名':[],'性别':[],'出生年月':[],'政治面貌':[],'毕业院校':[],'毕业专业':[],'最高学历':[],
                      '职务':[],'职称':[],'联系方式':[],'邮箱':[],'电子邮箱':[], '自我简介':[],'科研成果':[]}
        # 该字典用于将外交老师的key转化为中文，便于后续的DataFrame输出
        sub_dict = {'Name':'姓名','Sex':'性别','Graduated':'毕业院校','Duties':'职务',
                            'Email':'联系方式', 'Job title':'职称','邮箱':'联系方式','电子邮箱':'联系方式'}
        # 该url是外教老师的url，由于外教采用是英文也即半角模式，因此需要特殊处理
        # 由于外教老师的英文性，相关内容中会存在空格，因此这里利用下划线_做替换
        if url == 'http://finance.jxufe.edu.cn/news-show-3097.html':
            repl_resp = re.sub('<.+?>', '_', resp).replace('\u3000','').replace('\u200b','').replace('\xa0','').replace('&nbsp;','')
            symbol = ':'
            Basic_info = {'Name':[],'Sex':[],'出生年月':[],'政治面貌':[],'Graduated':[],'毕业专业':[],'最高学历':[],
                      'Duties':[],'Job title':[],'联系方式':[],'Email':[],'电子邮箱':[],'自我简介':[],'科研成果':[],'职称':[]}
        # 该url是杨超老师，由于杨超老师的数据结果过于分散，采用不同于一般老师的思路来处理，具体如下
        # 1. 以所有的p标签为准，利用re.sub用下划线_替换掉所有p标签
        # 2. 将剩余的标签替换为空
        elif url == 'http://finance.jxufe.edu.cn/news-show-2847.html':
            repl_resp = re.sub('</?p.+?>', '_', resp).replace('\u3000','').replace('\u200b','').replace('\xa0','').replace('&nbsp;','')
            repl_resp = re.sub('<.+?>', '', repl_resp)
            
        # 将正文信息提取出来
        All_info = re.findall(r'>>正文(.+)版权所有', repl_resp, re.DOTALL)[0]
        for item in list(Basic_info.keys())[:-2]:
            # 该字符串的作用是为了应付如下情况
            # 由于之前采用的空格替换，因此对于key中有空格的情况无法顺利处理，由此以\s重组key也即item，使其能够匹配如下情况
            sub_item = '\s*'.join(item)
            try:
                # 一般老师的处理
                if symbol == '：' and url != 'http://finance.jxufe.edu.cn/news-show-2847.html':
                    content = re.findall('{}\\s*{}(\\S+)'.format(sub_item, symbol+'\\s*'), All_info)[0]
                
                # 外教和杨超老师的处理
                elif symbol == ':' or url == 'http://finance.jxufe.edu.cn/news-show-2847.html':
                    content = re.findall(r'{}\s*{}\s*_*([^_*]+)'.format(item, symbol), All_info, re.DOTALL)[0]
                
                # 提取邮箱，将邮箱放入指定的key中，即联系方式中
                if re.match(r'\w+@\w+(?:\.\w+)', content):
                    Basic_info['联系方式'] = content
                    # 这里删除的外教dict的key—Email，综合来讲，目的就是为了所有老师的字典有相同的key
                    if re.match(r'[A-Za-z]+', item).group(0) == 'Email':
                        del Basic_info[item]
                    continue
                
                # 如果内容不为空，就保存至字典中
                if len(content) != 0:
                    # 外教老师的处理，同样也删去了key
                    if symbol == ':':
                        Basic_info[sub_dict[item]] = content
                        del Basic_info[item]
                    else:
                    # 一般老师的处理
                        Basic_info[item] = content
                else:
                    print(item,'查询失败')
            except:
                # 总会有些老师不存在一些key，所有try中的正则会匹配失败，但为了保持程序继续运作，用try-except捕获了而已，并不影响程序的效果
                # 同时为了不影响输出的美观性，这里就省略了print
#                 print(item,'不存在')
                Basic_info[item] = '无'
        
        # 用于匹配后文中的自我介绍以及科研成果的匹配
        # 但是这里我并没有用正则匹配，因为我想尝试一下老师之前讲过的一种方法，加强一下这种方法的利用
        # 也即利用text.index()找到特殊文字的位置，来索引对应文字
        # 这里的key_dict就是为了不同情况的关键词
        key_dict = {'自我简介':[], '工作经历':[], '开设课程':[], 'Education':[], '科研成果':[], '代表性论文':[], '主要成果':[], 'Major Research Publications':[]}
        for key in list(key_dict.keys()):
            try:
                key_dict[key] = [All_info.index(key), All_info.index(key)+len(key)]
            except:
                # 这里把值设为9999是为了后续的最小索引匹配，9999是个很大数，已经超过了总体文字的范围
#                 print('没有该%s关键词' % key)
                key_dict[key] = [9999]
        # 找到最小的那个索引
        # 其原理是，索引更小的，肯定是更在前面的文字，因此也会包含同类别下索引更大的文字，因此以这个最小的为准
        min_self = min(key_dict['自我简介']+key_dict['开设课程']+key_dict['Education']+key_dict['工作经历'])
        min_research = min(key_dict['代表性论文']+key_dict['科研成果']+key_dict['Major Research Publications']+key_dict['主要成果'])
        # 索引套取
        self_introduction = All_info[min_self:min_research]
        research = All_info[min_research:]
        
        Basic_info['自我简介'] = self_introduction.replace('_','')
        Basic_info['科研成果'] = research.replace('_','')
        
        # 删掉字典中多余的key
        try:
            del Basic_info['邮箱']
        except:
            pass
        try:
            del Basic_info['电子邮箱']
        except:
            pass

        List_info.append(Basic_info)

df_info = pd.DataFrame(List_info, columns=['姓名', '性别','出生年月','政治面貌','毕业院校','毕业专业','最高学历','职务','职称','联系方式','自我简介','科研成果'])
display(HTML(df_info.to_html()))

3
